In [2]:
import pandas as pd
import os
import numpy as np
from matplotlib import pyplot as plt
from PIL import Image

In [30]:
# define file locations
lidc_dir = '../../LIDC/'
yolo_dir = '../../LIDC_YOLO/'

In [27]:
df = pd.read_csv('nodule_locations.csv') # load location of nodules
df['case'] = df['case'].astype(str).str.zfill(4)
df.head(10) # x loc, y loc is center of nodule

case     scan  roi   volume  eq. diam.  x loc.  y loc.  slice no.  \
0  0001  3000566    1  6459.75     23.107     317     367         43   
1  0002  3000522    1  6663.44     23.347     345     361         77   
2  0003  3000611    1   408.79      9.208     308     198         57   
3  0003  3000611    2  1165.82     13.058     221     219         56   
4  0003  3000611    3  4989.64     21.201     367     350         65   
5  0003  3000611    4  4276.35     20.138     369     347         74   
6  0004  3000534    1    58.32      4.811     142     323        165   
7  0005  3000548    1   115.76      6.047     313     407         53   
8  0005  3000548    2    76.07      5.257     127     398         56   
9  0005  3000548    3    69.45      5.100     407     377         45   

   Unnamed: 8        nodIDs   Unnamed: 10   Unnamed: 11  Unnamed: 12  \
0         NaN  IL057_127364    Nodule 001   MI014_12127            0   
1         NaN             8   MI014_11691           NaN          NaN   
2         NaN    Nodule 003  IL057_130602             8  MI014_16599   
3         NaN  IL057_130598    Nodule 002             9  MI014_16595   
4         NaN             0  IL057_130591    Nodule 001  MI014_16588   
5         NaN            12           NaN           NaN          NaN   
6         NaN  IL057_132683   MI014_16178    Nodule 001            0   
7         NaN  IL057_123066    Nodule 002             3  MI014_11887   
8         NaN   MI014_11888    Nodule 001  IL057_123070            0   
9         NaN    Nodule 004           NaN           NaN          NaN   

  Unnamed: 13 Unnamed: 14 Unnamed: 15  
0         NaN         NaN         NaN  
1         NaN         NaN         NaN  
2         NaN         NaN         NaN  
3         NaN         NaN         NaN  
4         NaN         NaN         NaN  
5         NaN         NaN         NaN  
6         NaN         NaN         NaN  
7         NaN         NaN         NaN  
8         NaN         NaN         NaN  
9         NaN         NaN         NaN

In [25]:
# get filepaths of all images, store in imgs
imgs = []
for root, dirs, files in os.walk(lidc_dir + 'images_full'):
    for file in files:
        if 'LIDC-IDRI' in file:
            imgs.append(os.path.join(root, file))

In [39]:
imgs

['../../LIDC/images_full/validation/LIDC-IDRI-0635_NI000_slice001.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0334_NI000_slice001.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0299_NI002_slice005.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0249_NI001_slice003.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0162_NI001_slice003.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0404_NI003_slice010.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0869_NI003_slice001.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0124_NI014_slice002.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0388_NI000_slice002.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0837_NI002_slice004.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0921_NI003_slice015.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0815_NI000_slice006.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0195_NI004_slice001.png',
 '../../LIDC/images_full/validation/LIDC-IDRI-0153_NI000_slice00

In [34]:
img_dir = 'LIDC-IDRI-0001-img'
mask_dir = 'LIDC-IDRI-0001-mask'

In [ ]:
# for every nodule in nodule_locations.csv, generate bbox nodule image and text file. 
for i, row in df.iterrows():
    for img in imgs:
        if row['case'] in img:
            # open corresponding image and mask file
            image = Image.open(img)
            mask = Image.open(img.replace('images_full', 'annotations_full'))

            # get nodule coords, roi, img size
            x, y, roi = row['x loc.'], row['y loc.'], row['roi']
            width, height = image.size

            # define bbox coords
            bbox = (x - 32, y - 32, x + 32, y + 32)

            # crop bbox
            image_crop = image.crop(bbox)
            mask_crop = mask.crop(bbox)

            # rename bbox with nodule ROI
            nodule = os.path.splitext(img)[0] + '_nodule' + str(roi) + '.png'
            nodule_image = nodule.replace('images_full', 'images')
            nodule_mask = nodule.replace('images_full', 'annotations')

            print(nodule_image)
            print(nodule_mask)

            image_crop.save(nodule_image, 'PNG')
            mask_crop.save(nodule_mask, 'PNG')

            # define text file name
            filename = os.path.splitext(os.path.basename(img))[0] + '.txt'

            if 'training' in img:    
                filepath = os.path.join(yolo_dir, 'train/labels', filename)
            elif 'testing' in img:
                filepath = os.path.join(yolo_dir, 'test/labels', filename)
            else:
                filepath = os.path.join(yolo_dir, 'valid/labels', filename)

            # if file doesn't exist, create, else append on a new line
            with open(filepath, 'a+') as f:
                # norm coords in yolo format
                x_norm, y_norm, w_norm, h_norm = x / width, y / height, 64 / width, 64 / height
                label = f'0 {x_norm:.6f} {y_norm:.6f} {w_norm:.6f} {h_norm:.6f}\n'

                # write to file
                f.write(label)

In [44]:
# for every nodule in nodule_locations.csv, generate bbox nodule image and text file. 
for i, row in df.iterrows():
    for img in imgs:
        if row['case'] in img:
            # open corresponding image and mask file
            image = Image.open(img)
            mask = Image.open(img.replace('images_full', 'annotations_full'))

            # get nodule coords, roi, img size
            x, y, roi = row['x loc.'], row['y loc.'], row['roi']
            width, height = image.size

            # define bbox coords
            bbox = (x - 32, y - 32, x + 32, y + 32)

            # crop bbox
            image_crop = image.crop(bbox)
            mask_crop = mask.crop(bbox)

            # rename bbox with nodule ROI
            nodule = os.path.splitext(img)[0] + '_nodule' + str(roi) + '.png'
            nodule_image = nodule.replace('images_full', 'images')
            nodule_mask = nodule.replace('images_full', 'annotations')

            print(nodule_image)
            print(nodule_mask)

            image_crop.save(nodule_image, 'PNG')
            mask_crop.save(nodule_mask, 'PNG')

            # define text file name
            filename = os.path.splitext(os.path.basename(img))[0] + '.txt'

            if 'training' in img:    
                filepath = os.path.join(yolo_dir, 'train/labels', filename)
            elif 'testing' in img:
                filepath = os.path.join(yolo_dir, 'test/labels', filename)
            else:
                filepath = os.path.join(yolo_dir, 'valid/labels', filename)

            # if file doesn't exist, create, else append on a new line
            with open(filepath, 'a+') as f:
                # norm coords in yolo format
                x_norm, y_norm, w_norm, h_norm = x / width, y / height, 64 / width, 64 / height
                label = f'0 {x_norm:.6f} {y_norm:.6f} {w_norm:.6f} {h_norm:.6f}\n'

                # write to file
                f.write(label)

../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice006_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice006_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice001_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice001_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice000_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice000_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice007_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice007_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice004_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice004_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice003_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice003_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0001_NI000_slice002_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0001_NI000_slice002_nodule1.png

../../LIDC/images/training/LIDC-IDRI-0003_NI002_slice001_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI002_slice001_nodule2.png
../../LIDC/images/training/LIDC-IDRI-0003_NI000_slice002_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI000_slice002_nodule2.png
../../LIDC/images/training/LIDC-IDRI-0003_NI000_slice005_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI000_slice005_nodule2.png
../../LIDC/images/training/LIDC-IDRI-0003_NI001_slice005_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI001_slice005_nodule2.png
../../LIDC/images/training/LIDC-IDRI-0003_NI001_slice002_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI001_slice002_nodule2.png
../../LIDC/images/training/LIDC-IDRI-0003_NI003_slice005_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI003_slice005_nodule2.png
../../LIDC/images/training/LIDC-IDRI-0003_NI003_slice002_nodule2.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI003_slice002_nodule2.png

../../LIDC/images/training/LIDC-IDRI-0003_NI000_slice003_nodule4.png
../../LIDC/annotations/training/LIDC-IDRI-0003_NI000_slice003_nodule4.png
../../LIDC/images/training/LIDC-IDRI-0004_NI000_slice002_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0004_NI000_slice002_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0005_NI000_slice001_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0005_NI000_slice001_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0005_NI001_slice001_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0005_NI001_slice001_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0005_NI002_slice001_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0005_NI002_slice001_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0005_NI002_slice000_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0005_NI002_slice000_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0005_NI000_slice000_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0005_NI000_slice000_nodule1.png

../../LIDC/images/training/LIDC-IDRI-0007_NI001_slice011_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI001_slice011_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0007_NI001_slice008_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI001_slice008_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0007_NI000_slice006_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI000_slice006_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0007_NI001_slice006_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI001_slice006_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0007_NI000_slice008_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI000_slice008_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0007_NI001_slice010_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI001_slice010_nodule1.png
../../LIDC/images/training/LIDC-IDRI-0007_NI000_slice010_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-0007_NI000_slice010_nodule1.png

../../LIDC/images/testing/LIDC-IDRI-0010_NI002_slice001_nodule3.png
../../LIDC/annotations/testing/LIDC-IDRI-0010_NI002_slice001_nodule3.png
../../LIDC/images/validation/LIDC-IDRI-0011_NI000_slice000_nodule1.png
../../LIDC/annotations/validation/LIDC-IDRI-0011_NI000_slice000_nodule1.png
../../LIDC/images/validation/LIDC-IDRI-0011_NI009_slice001_nodule1.png
../../LIDC/annotations/validation/LIDC-IDRI-0011_NI009_slice001_nodule1.png
../../LIDC/images/validation/LIDC-IDRI-0011_NI005_slice000_nodule1.png
../../LIDC/annotations/validation/LIDC-IDRI-0011_NI005_slice000_nodule1.png
../../LIDC/images/validation/LIDC-IDRI-0011_NI002_slice001_nodule1.png
../../LIDC/annotations/validation/LIDC-IDRI-0011_NI002_slice001_nodule1.png
../../LIDC/images/validation/LIDC-IDRI-0011_NI000_slice001_nodule1.png
../../LIDC/annotations/validation/LIDC-IDRI-0011_NI000_slice001_nodule1.png
../../LIDC/images/validation/LIDC-IDRI-0011_NI005_slice001_nodule1.png
../../LIDC/annotations/validation/LIDC-IDRI-0011_NI00

...

../../LIDC/images/testing/LIDC-IDRI-1005_NI005_slice003_nodule1.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI005_slice003_nodule1.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI000_slice003_nodule1.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI000_slice003_nodule1.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI002_slice000_nodule2.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI002_slice000_nodule2.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI001_slice000_nodule2.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI001_slice000_nodule2.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI000_slice000_nodule2.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI000_slice000_nodule2.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI000_slice001_nodule2.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI000_slice001_nodule2.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI001_slice001_nodule2.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI001_slice001_nodule2.png
../../LIDC/im

../../LIDC/images/testing/LIDC-IDRI-1005_NI004_slice001_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI004_slice001_nodule5.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI005_slice005_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI005_slice005_nodule5.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI000_slice002_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI000_slice002_nodule5.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI001_slice002_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI001_slice002_nodule5.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI003_slice002_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI003_slice002_nodule5.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI002_slice002_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI002_slice002_nodule5.png
../../LIDC/images/testing/LIDC-IDRI-1005_NI005_slice004_nodule5.png
../../LIDC/annotations/testing/LIDC-IDRI-1005_NI005_slice004_nodule5.png
../../LIDC/im

../../LIDC/images/validation/LIDC-IDRI-1007_NI000_slice000_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-1007_NI000_slice000_nodule2.png
../../LIDC/images/validation/LIDC-IDRI-1007_NI001_slice010_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-1007_NI001_slice010_nodule2.png
../../LIDC/images/validation/LIDC-IDRI-1007_NI000_slice001_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-1007_NI000_slice001_nodule2.png
../../LIDC/images/validation/LIDC-IDRI-1007_NI001_slice008_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-1007_NI001_slice008_nodule2.png
../../LIDC/images/validation/LIDC-IDRI-1007_NI001_slice006_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-1007_NI001_slice006_nodule2.png
../../LIDC/images/validation/LIDC-IDRI-1007_NI001_slice001_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-1007_NI001_slice001_nodule2.png
../../LIDC/images/validation/LIDC-IDRI-1007_NI001_slice002_nodule2.png
../../LIDC/annotations/validation/LIDC-IDRI-100

../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice002_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice002_nodule1.png
../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice005_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice005_nodule1.png
../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice012_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice012_nodule1.png
../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice004_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice004_nodule1.png
../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice003_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice003_nodule1.png
../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice000_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice000_nodule1.png
../../LIDC/images/training/LIDC-IDRI-1009_NI000_slice007_nodule1.png
../../LIDC/annotations/training/LIDC-IDRI-1009_NI000_slice007_nodule1.png

../../LIDC/images/training/LIDC-IDRI-1011_NI002_slice000_nodule3.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI002_slice000_nodule3.png
../../LIDC/images/training/LIDC-IDRI-1011_NI002_slice001_nodule3.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI002_slice001_nodule3.png
../../LIDC/images/training/LIDC-IDRI-1011_NI001_slice006_nodule3.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI001_slice006_nodule3.png
../../LIDC/images/training/LIDC-IDRI-1011_NI001_slice001_nodule3.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI001_slice001_nodule3.png
../../LIDC/images/training/LIDC-IDRI-1011_NI000_slice001_nodule3.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI000_slice001_nodule3.png
../../LIDC/images/training/LIDC-IDRI-1011_NI000_slice006_nodule3.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI000_slice006_nodule3.png
../../LIDC/images/training/LIDC-IDRI-1011_NI002_slice002_nodule4.png
../../LIDC/annotations/training/LIDC-IDRI-1011_NI002_slice002_nodule4.png